# 3+1 Simon-Mars tensor in Kerr spacetime

This notebook demonstrates a few capabilities of [SageManifolds](https://sagemanifolds.obspm.fr) (version 1.3, as included in SageMath 8.3) in computations regarding 3+1 slicing of Kerr spacetime. In particular, it implements the computation of the 3+1 decomposition of the Simon-Mars tensor as given in the article [arXiv:1412.6542](http://arxiv.org/abs/1412.6542).

Click [here](https://raw.githubusercontent.com/sagemanifolds/SageManifolds/master/Worksheets/v1.3/SM_Simon-Mars_3p1_Kerr.ipynb) to download the notebook file (ipynb format). To run it, you must start SageMath with the Jupyter notebook, via the command `sage -n jupyter`

*NB:* a version of SageMath at least equal to 8.2 is required to run this notebook:

In [1]:
version()

'SageMath version 8.3, Release Date: 2018-08-03'

First we set up the notebook to display mathematical objects using LaTeX rendering:

In [2]:
%display latex

Since some computations are quite long, we ask for running them in parallel on 8 cores:

In [3]:
Parallelism().set(nproc=8)

## Spacelike hypersurface

We consider some hypersurface $\Sigma$ of a spacelike foliation $(\Sigma_t)_{t\in\mathbb{R}}$ of Kerr spacetime; we declare $\Sigma_t$ as a 3-dimensional Riemannian manifold:

In [4]:
Sig = Manifold(3, 'Sigma', latex_name=r'\Sigma', 
               structure='Riemannian', metric_name='gam', 
               metric_latex_name=r'\gamma', start_index=1)

On $\Sigma$, we consider the *"rational-polynomial" coordinates* $(r,y,\phi)$ inheritated from the standard Boyer-Lindquist coordinates $(t,r,\theta,\phi)$ of Kerr spacetime, via $y=\cos\theta$:

In [5]:
X.<r,y,ph> = Sig.chart(r'r:(1,+oo) y:(-1,1) ph:(0,2*pi):\phi')
print(X) ; X

Chart (Sigma, (r, y, ph))


Chart (Sigma, (r, y, ph))

<p>The two Kerr parameters:</p>

In [6]:
var('m, a', domain='real')
assume(m > 0)
assume(a > 0)
assume(a^2-2*m*r+r^2 > 0)  # region where Sigma is spacelike

<h3>Riemannian metric on $\Sigma$</h3>
<p>The variables introduced so far satisfy the following assumptions:</p>

<p>Without any loss of generality (for $m\not =0$), we may set $m=1$:</p>

In [7]:
#m=1
#assume(a<1)

In [8]:
#a=1 # extreme Kerr

<p>The variables introduced so far obey the following assumptions:</p>

In [9]:
assumptions()

[r is real,
 r > 1,
 y is real,
 y > -1,
 y < 1,
 ph is real,
 ph > 0,
 ph < 2*pi,
 m is real,
 a is real,
 m > 0,
 a > 0,
 a^2 - 2*m*r + r^2 > 0]

<p>Some shortcut notations:</p>

In [10]:
rho2 = r^2 + a^2*y^2 
Del = r^2 -2*m*r + a^2
AA2 = rho2*(r^2 + a^2) + 2*a^2*m*r*(1-y^2)
BB2 = r^2 + a^2 + 2*a^2*m*r*(1-y^2)/rho2

<p>The metric $h$ induced by the spacetime metric $g$ on $\Sigma$:</p>

In [11]:
gam = Sig.riemannian_metric('gam', latex_name=r'\gamma') 
gam[1,1] = rho2/Del
gam[2,2] = rho2/(1-y^2)
gam[3,3] = BB2*(1-y^2)
gam.display()

gam = (a^2*y^2 + r^2)/(a^2 - 2*m*r + r^2) dr*dr - (a^2*y^2 + r^2)/(y^2 - 1) dy*dy + (2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(y^2 - 1) dph*dph

<p>A matrix view of the components w.r.t. coordinates $(r,y,\phi)$:</p>

In [12]:
gam[:]

[                        (a^2*y^2 + r^2)/(a^2 - 2*m*r + r^2)                                                           0                                                           0]
[                                                          0                                  -(a^2*y^2 + r^2)/(y^2 - 1)                                                           0]
[                                                          0                                                           0 (2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(y^2 - 1)]

<h3>Lapse function and shift vector</h3>

In [13]:
N = Sig.scalar_field(sqrt(Del / BB2), name='N')
print(N)
N.display()

Scalar field N on the 3-dimensional Riemannian manifold Sigma


N: Sigma --> R
   (r, y, ph) |--> sqrt(-(a^2 - 2*m*r + r^2)/(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2))

In [14]:
b = Sig.vector_field('beta', latex_name=r'\beta') 
b[3] = -2*m*r*a/AA2   
# unset components are zero 
b.display()

beta = 2*a*m*r/(2*(y^2 - 1)*a^2*m*r - (a^2*y^2 + r^2)*(a^2 + r^2)) d/dph

<h3>Extrinsic curvature of $\Sigma$</h3>
<p>We use the formula $$ K_{ij} = \frac{1}{2N} \mathcal{L}_{\beta} \gamma_{ij}$$ which is valid for any stationary spacetime:</p>

In [15]:
K = gam.lie_der(b) / (2*N)
K.set_name('K')
print(K) ; K.display()

Field of symmetric bilinear forms K on the 3-dimensional Riemannian manifold Sigma


K = (a^3*m*r^2 + 3*a*m*r^4 + (a^5*m - a^3*m*r^2)*y^4 - (a^5*m + 3*a*m*r^4)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) dr*dph - 2*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*((a^5*m*r - 2*a^3*m^2*r^2 + a^3*m*r^3)*y^3 - (a^5*m*r - 2*a^3*m^2*r^2 + a^3*m*r^3)*y)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) dy*dph + (a^3*m*r^2 + 3*a*m*r^4 + (a^5*m - a^3*m*r^2)*y^4 - (a^5*m + 3*a*m*r^4)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) dph*dr - 2*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*((a^5*m*r - 2*a^3*m^2*r^2 + a^3*m*r^3)*y^3 - (a^5*m*r - 2*a^3*m^2*r^2 + a^3*m*r^3)*y)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) dph*dy

<p>Check (comparison with known formulas):</p>

In [16]:
Krp = a*m*(1-y^2)*(3*r^4+a^2*r^2+a^2*(r^2-a^2)*y^2) / rho2^2/sqrt(Del*BB2)
Krp

((a^2 - r^2)*a^2*y^2 - a^2*r^2 - 3*r^4)*(y^2 - 1)*a*m/((a^2*y^2 + r^2)^2*sqrt(-(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(a^2 - 2*m*r + r^2)))

In [17]:
K[1,3] - Krp

0

In [18]:
Kyp = 2*m*r*a^3*(1-y^2)*y*sqrt(Del)/rho2^2/sqrt(BB2)
Kyp

-2*sqrt(a^2 - 2*m*r + r^2)*(y^2 - 1)*a^3*m*r*y/(sqrt(-2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) + a^2 + r^2)*(a^2*y^2 + r^2)^2)

In [19]:
K[2,3] - Kyp

0

<p>For now on, we use the expressions Krp and Kyp above for $K_{r\phi}$ and $K_{ry}$, respectively:</p>

In [20]:
K1 = Sig.sym_bilin_form_field('K')
K1[1,3] = Krp
K1[2,3] = Kyp
K = K1
K.display()

K = ((a^2 - r^2)*a^2*y^2 - a^2*r^2 - 3*r^4)*(y^2 - 1)*a*m/((a^2*y^2 + r^2)^2*sqrt(-(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(a^2 - 2*m*r + r^2))) dr*dph - 2*sqrt(a^2 - 2*m*r + r^2)*(y^2 - 1)*a^3*m*r*y/(sqrt(-2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) + a^2 + r^2)*(a^2*y^2 + r^2)^2) dy*dph + ((a^2 - r^2)*a^2*y^2 - a^2*r^2 - 3*r^4)*(y^2 - 1)*a*m/((a^2*y^2 + r^2)^2*sqrt(-(2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) - a^2 - r^2)*(a^2 - 2*m*r + r^2))) dph*dr - 2*sqrt(a^2 - 2*m*r + r^2)*(y^2 - 1)*a^3*m*r*y/(sqrt(-2*(y^2 - 1)*a^2*m*r/(a^2*y^2 + r^2) + a^2 + r^2)*(a^2*y^2 + r^2)^2) dph*dy

<p>The type-(1,1) tensor $K^\sharp$ of components $K^i_{\ \, j} = \gamma^{ik} K_{kj}$:</p>

In [21]:
Ku = K.up(gam, 0)
print(Ku) ; Ku.display()

Tensor field of type (1,1) on the 3-dimensional Riemannian manifold Sigma


(a^5*m*r^2 - 2*a^3*m^2*r^3 + 4*a^3*m*r^4 - 6*a*m^2*r^5 + 3*a*m*r^6 + (a^7*m - 2*a^5*m^2*r + 2*a^3*m^2*r^3 - a^3*m*r^4)*y^4 - (a^7*m - 2*a^5*m^2*r + a^5*m*r^2 + 3*a^3*m*r^4 - 6*a*m^2*r^5 + 3*a*m*r^6)*y^2)*sqrt(a^2*y^2 + r^2)/((a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dr*dph + 2*(a^3*m*r*y^5 - 2*a^3*m*r*y^3 + a^3*m*r*y)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)/((a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)) d/dy*dph + (a^3*m*r^2 + 3*a*m*r^4 - (a^5*m - a^3*m*r^2)*y^2)*sqrt(a^2*y^2 + r^2)/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dph*dr + 2*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)*a^3*m*r*y/((2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)) d/dph*dy

<p>We may check that the hypersurface $\Sigma$ is maximal, i.e. that $K^k_{\ \, k} = 0$:</p>

In [22]:
trK = Ku.trace()
print(trK)

Scalar field zero on the 3-dimensional Riemannian manifold Sigma


<h3>Connection and curvature</h3>
<p>Let us call $D$ the Levi-Civita connection associated with $\gamma$: </p>

In [23]:
D = gam.connection(name='D')
print(D) ; D

Levi-Civita connection D associated with the Riemannian metric gam on the 3-dimensional Riemannian manifold Sigma


Levi-Civita connection D associated with the Riemannian metric gam on the 3-dimensional Riemannian manifold Sigma

<p>The Ricci tensor associated with $\gamma$:</p>

In [24]:
Ric = gam.ricci()
print(Ric) ; Ric

Field of symmetric bilinear forms Ric(gam) on the 3-dimensional Riemannian manifold Sigma


Field of symmetric bilinear forms Ric(gam) on the 3-dimensional Riemannian manifold Sigma

In [25]:
Ric[1,1]

-(5*a^6*m^2*r^4 + 2*a^4*m^2*r^6 + 8*a^4*m*r^7 - 7*a^2*m^2*r^8 + 7*a^2*m*r^9 + 2*m*r^11 + (a^10*m^2 + 3*a^10*m*r - 14*a^8*m^2*r^2 - 11*a^6*m^2*r^4 + 3*a^6*m*r^5 + 6*(a^8*m + 2*a^6*m^3)*r^3)*y^6 + (3*a^6*m - 4*a^4*m^3)*r^5 - (a^10*m^2 + 9*a^10*m*r - 30*a^8*m^2*r^2 - 35*a^6*m^2*r^4 - 16*a^4*m^2*r^6 + 4*a^4*m*r^7 + (17*a^6*m + 4*a^4*m^3)*r^5 + 2*(11*a^8*m + 12*a^6*m^3)*r^3)*y^4 - (16*a^8*m^2*r^2 + 29*a^6*m^2*r^4 + 18*a^4*m^2*r^6 + 16*a^4*m*r^7 - 7*a^2*m^2*r^8 + 5*a^2*m*r^9 + (17*a^6*m - 8*a^4*m^3)*r^5 + 6*(a^8*m - 2*a^6*m^3)*r^3)*y^2)/(4*a^6*m^2*r^6 + 6*a^4*m*r^9 + 3*a^2*r^12 - 2*m*r^13 + r^14 + (3*a^4 - 8*a^2*m^2)*r^10 + (a^6 - 4*a^4*m^2)*r^8 + (a^14 - 6*a^12*m*r - 6*a^8*m*r^5 + a^8*r^6 + 3*(a^10 + 4*a^8*m^2)*r^4 - 4*(3*a^10*m + 2*a^8*m^3)*r^3 + 3*(a^12 + 4*a^10*m^2)*r^2)*y^8 + 4*(a^6*m - 2*a^4*m^3)*r^7 + 4*(a^12*m*r - 5*a^6*m*r^7 + a^6*r^8 + (3*a^8 + 8*a^6*m^2)*r^6 - (9*a^8*m + 4*a^6*m^3)*r^5 + (3*a^10 + 4*a^8*m^2)*r^4 - (3*a^10*m - 4*a^8*m^3)*r^3 + (a^12 - 4*a^10*m^2)*r^2)*y^6 + 2*(2*a^10*m^2*r^2 + 16*a^6*m^3*r^5 - 12*a^4*m*r^9 + 3*a^4*r^10 + (9*a^6 + 14*a^4*m^2)*r^8 - 2*(9*a^6*m + 2*a^4*m^3)*r^7 + 3*(3*a^8 - 2*a^6*m^2)*r^6 + 3*(a^10 - 6*a^8*m^2)*r^4 + 2*(3*a^10*m - 2*a^8*m^3)*r^3)*y^4 + 4*(2*a^8*m^2*r^4 - 3*a^4*m*r^9 - 3*a^2*m*r^11 + a^2*r^12 + (3*a^4 + 2*a^2*m^2)*r^10 + 3*(a^6 - 2*a^4*m^2)*r^8 + (3*a^6*m + 4*a^4*m^3)*r^7 + (a^8 - 6*a^6*m^2)*r^6 + (3*a^8*m - 4*a^6*m^3)*r^5)*y^2)

In [26]:
Ric[1,2]

((3*a^10*m - 4*a^8*m^2*r + 6*a^8*m*r^2 - 8*a^6*m^2*r^3 + 3*a^6*m*r^4)*y^5 + 2*(2*a^8*m^2*r - 3*a^8*m*r^2 + 12*a^6*m^2*r^3 - 6*a^6*m*r^4 + 6*a^4*m^2*r^5 - 3*a^4*m*r^6)*y^3 - (16*a^6*m^2*r^3 + 9*a^6*m*r^4 + 12*a^4*m^2*r^5 + 18*a^4*m*r^6 + 9*a^2*m*r^8)*y)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 + (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^8 + 4*(a^10*m*r - 2*a^8*m*r^3 - 3*a^6*m*r^5 + a^6*r^6 + 2*(a^8 + a^6*m^2)*r^4 + (a^10 - 2*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^4*m*r^7 + 3*a^4*r^8 + 2*(3*a^6 + a^4*m^2)*r^6 + (3*a^8 - 8*a^6*m^2)*r^4)*y^4 + 4*(2*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*a^4*m*r^7 + 2*a^4*r^8 - a^2*m*r^9 + a^2*r^10 + (a^6 - 2*a^4*m^2)*r^6)*y^2)

In [27]:
Ric[1,3]

0

In [28]:
Ric[2,2]

(6*a^6*m^2*r^4 + 4*a^4*m^2*r^6 + 7*a^4*m*r^7 - 2*a^2*m^2*r^8 + 5*a^2*m*r^9 + m*r^11 + 2*(3*a^10*m*r - 10*a^8*m^2*r^2 - 10*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*(3*a^8*m + 4*a^6*m^3)*r^3)*y^6 + (3*a^6*m - 8*a^4*m^3)*r^5 - (9*a^10*m*r - 34*a^8*m^2*r^2 - 36*a^6*m^2*r^4 - 2*a^4*m^2*r^6 - a^4*m*r^7 + (7*a^6*m + 8*a^4*m^3)*r^5 + (17*a^8*m + 32*a^6*m^3)*r^3)*y^4 - 2*(7*a^8*m^2*r^2 + 11*a^6*m^2*r^4 + 3*a^4*m^2*r^6 + 7*a^4*m*r^7 - a^2*m^2*r^8 + 2*a^2*m*r^9 + 8*(a^6*m - a^4*m^3)*r^5 + (3*a^8*m - 8*a^6*m^3)*r^3)*y^2)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 - (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^10 + (a^12 - 8*a^10*m*r + 4*a^8*m*r^3 + 12*a^6*m*r^5 - 4*a^6*r^6 - (7*a^8 + 8*a^6*m^2)*r^4 - 2*(a^10 - 6*a^8*m^2)*r^2)*y^8 + 2*(2*a^10*m*r - 10*a^8*m*r^3 - 6*a^6*m*r^5 + 6*a^4*m*r^7 - 3*a^4*r^8 - 2*(2*a^6 + a^4*m^2)*r^6 + (a^8 + 12*a^6*m^2)*r^4 + 2*(a^10 - 3*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^6*m*r^5 - 10*a^4*m*r^7 - a^4*r^8 + 2*a^2*m*r^9 - 2*a^2*r^10 + 2*(2*a^6 + 3*a^4*m^2)*r^6 + 3*(a^8 - 4*a^6*m^2)*r^4)*y^4 + (8*a^6*m^2*r^4 + 12*a^6*m*r^5 + 4*a^4*m*r^7 + 7*a^4*r^8 - 8*a^2*m*r^9 + 2*a^2*r^10 - r^12 + 4*(a^6 - 3*a^4*m^2)*r^6)*y^2)

In [29]:
Ric[2,3]

0

In [30]:
Ric[3,3]

(a^6*m^2*r^4 + 4*a^4*m^3*r^5 + 10*a^4*m^2*r^6 + a^4*m*r^7 + 13*a^2*m^2*r^8 + 2*a^2*m*r^9 + m*r^11 + (a^10*m^2 + 3*a^10*m*r - 18*a^8*m^2*r^2 - 15*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*(3*a^8*m + 10*a^6*m^3)*r^3)*y^8 - (2*a^10*m^2 + 3*a^10*m*r - 38*a^8*m^2*r^2 - 22*a^6*m^2*r^4 + 2*a^4*m^2*r^6 - 5*a^4*m*r^7 - (7*a^6*m - 4*a^4*m^3)*r^5 + (a^8*m + 60*a^6*m^3)*r^3)*y^6 + (a^10*m^2 - 22*a^8*m^2*r^2 + 2*a^6*m^2*r^4 + 14*a^4*m^2*r^6 - 3*a^4*m*r^7 + 13*a^2*m^2*r^8 + a^2*m*r^9 - 3*(3*a^6*m - 4*a^4*m^3)*r^5 - 5*(a^8*m - 12*a^6*m^3)*r^3)*y^4 + (2*a^8*m^2*r^2 - 20*a^6*m^3*r^3 - 10*a^6*m^2*r^4 - 22*a^4*m^2*r^6 - 3*a^4*m*r^7 - 26*a^2*m^2*r^8 - 3*a^2*m*r^9 - m*r^11 - (a^6*m + 12*a^4*m^3)*r^5)*y^2)/(2*a^2*m*r^9 + a^2*r^10 + r^12 + (a^12 - 2*a^10*m*r + a^10*r^2)*y^10 + (2*a^10*m*r + 5*a^10*r^2 - 8*a^8*m*r^3 + 5*a^8*r^4)*y^8 + 2*(4*a^8*m*r^3 + 5*a^8*r^4 - 6*a^6*m*r^5 + 5*a^6*r^6)*y^6 + 2*(6*a^6*m*r^5 + 5*a^6*r^6 - 4*a^4*m*r^7 + 5*a^4*r^8)*y^4 + (8*a^4*m*r^7 + 5*a^4*r^8 - 2*a^2*m*r^9 + 5*a^2*r^10)*y^2)

<p>The scalar curvature $R = \gamma^{ij} R_{ij}$:</p>

In [31]:
R = gam.ricci_scalar(name='R')
print(R)
R.display()

Scalar field R on the 3-dimensional Riemannian manifold Sigma


R: Sigma --> R
   (r, y, ph) |--> 2*(a^6*m^2*r^4 + 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8 - (a^10*m^2 - 6*a^8*m^2*r^2 + 8*a^6*m^3*r^3 - 3*a^6*m^2*r^4)*y^6 + (a^10*m^2 - 8*a^8*m^2*r^2 + 16*a^6*m^3*r^3 - 3*a^6*m^2*r^4 - 6*a^4*m^2*r^6)*y^4 + (2*a^8*m^2*r^2 - 8*a^6*m^3*r^3 - a^6*m^2*r^4 - 9*a^2*m^2*r^8)*y^2)/(4*a^4*m^2*r^8 + 4*a^4*m*r^9 + a^4*r^10 + 4*a^2*m*r^11 + 2*a^2*r^12 + r^14 + (a^14 - 4*a^12*m*r - 4*a^10*m*r^3 + a^10*r^4 + 2*(a^12 + 2*a^10*m^2)*r^2)*y^10 + (4*a^12*m*r - 12*a^10*m*r^3 - 16*a^8*m*r^5 + 5*a^8*r^6 + 2*(5*a^10 + 6*a^8*m^2)*r^4 + (5*a^12 - 8*a^10*m^2)*r^2)*y^8 + 2*(2*a^10*m^2*r^2 + 8*a^10*m*r^3 - 4*a^8*m*r^5 - 12*a^6*m*r^7 + 5*a^6*r^8 + 2*(5*a^8 + 3*a^6*m^2)*r^6 + (5*a^10 - 12*a^8*m^2)*r^4)*y^6 + 2*(6*a^8*m^2*r^4 + 12*a^8*m*r^5 + 4*a^6*m*r^7 - 8*a^4*m*r^9 + 5*a^4*r^10 + 2*(5*a^6 + a^4*m^2)*r^8 + (5*a^8 - 12*a^6*m^2)*r^6)*y^4 + (12*a^6*m^2*r^6 + 16*a^6*m*r^7 + 12*a^4*m*r^9 + 10*a^4*r^10 - 4*a^2*m*r^11 + 5*a^2*r^12 + (5*a^6 - 8*a^4*m^2)*r^8)*y^2)

<h2>Test: 3+1 Einstein equations</h2>
<p>Let us check that the vacuum 3+1 Einstein equations are satisfied.</p>
<p>We start by the contraint equations:</p>
<h3>Hamiltonian constraint</h3>
<p>Let us first evaluate the term $K_{ij} K^{ij}$:</p>

In [32]:
Kuu = Ku.up(gam, 1)
trKK = K['_ij']*Kuu['^ij']
print(trKK) ; trKK.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> 2*(a^6*m^2*r^4 + 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8 - (a^10*m^2 - 6*a^8*m^2*r^2 + 8*a^6*m^3*r^3 - 3*a^6*m^2*r^4)*y^6 + (a^10*m^2 - 8*a^8*m^2*r^2 + 16*a^6*m^3*r^3 - 3*a^6*m^2*r^4 - 6*a^4*m^2*r^6)*y^4 + (2*a^8*m^2*r^2 - 8*a^6*m^3*r^3 - a^6*m^2*r^4 - 9*a^2*m^2*r^8)*y^2)/(4*a^4*m^2*r^8 + 4*a^4*m*r^9 + a^4*r^10 + 4*a^2*m*r^11 + 2*a^2*r^12 + r^14 + (a^14 - 4*a^12*m*r - 4*a^10*m*r^3 + a^10*r^4 + 2*(a^12 + 2*a^10*m^2)*r^2)*y^10 + (4*a^12*m*r - 12*a^10*m*r^3 - 16*a^8*m*r^5 + 5*a^8*r^6 + 2*(5*a^10 + 6*a^8*m^2)*r^4 + (5*a^12 - 8*a^10*m^2)*r^2)*y^8 + 2*(2*a^10*m^2*r^2 + 8*a^10*m*r^3 - 4*a^8*m*r^5 - 12*a^6*m*r^7 + 5*a^6*r^8 + 2*(5*a^8 + 3*a^6*m^2)*r^6 + (5*a^10 - 12*a^8*m^2)*r^4)*y^6 + 2*(6*a^8*m^2*r^4 + 12*a^8*m*r^5 + 4*a^6*m*r^7 - 8*a^4*m*r^9 + 5*a^4*r^10 + 2*(5*a^6 + a^4*m^2)*r^8 + (5*a^8 - 12*a^6*m^2)*r^6)*y^4 + (12*a^6*m^2*r^6 + 16*a^6*m*r^7 + 12*a^4*m*r^9 + 10*a^4*r^10 - 4*a^2*m*r^11 + 5*a^2*r^12 + (5*a^6 - 8*a^4*m^2)*r^8)*y^2)

<p>The vacuum Hamiltonian constraint equation is $$R + K^2 -K_{ij} K^{ij} = 0 $$</p>

In [33]:
Ham = R + trK^2 - trKK
print(Ham) ; Ham.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> 0

<h3>Momentum constraint</h3>
<p>In vaccum, the momentum constraint is $$ D_j K^j_{\ \, i} - D_i K = 0 $$</p>

In [34]:
mom = D(Ku).trace(0,2) - D(trK)
print(mom)
mom.display()

1-form on the 3-dimensional Riemannian manifold Sigma


0

<h3>Dynamical Einstein equations</h3>
<p>Let us first evaluate the symmetric bilinear form $k_{ij} := K_{ik} K^k_{\ \, j}$:</p>

In [35]:
KK = K['_ik']*Ku['^k_j']
print(KK)

Tensor field of type (0,2) on the 3-dimensional Riemannian manifold Sigma


In [36]:
KK1 = KK.symmetrize()
KK == KK1

True

In [37]:
KK = KK1
print(KK)

Field of symmetric bilinear forms on the 3-dimensional Riemannian manifold Sigma


In [38]:
KK[1,1]

(a^6*m^2*r^4 + 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8 - (a^10*m^2 - 2*a^8*m^2*r^2 + a^6*m^2*r^4)*y^6 + (a^10*m^2 + 5*a^6*m^2*r^4 - 6*a^4*m^2*r^6)*y^4 - (2*a^8*m^2*r^2 + 5*a^6*m^2*r^4 + 9*a^2*m^2*r^8)*y^2)/(4*a^6*m^2*r^6 + 6*a^4*m*r^9 + 3*a^2*r^12 - 2*m*r^13 + r^14 + (3*a^4 - 8*a^2*m^2)*r^10 + (a^6 - 4*a^4*m^2)*r^8 + (a^14 - 6*a^12*m*r - 6*a^8*m*r^5 + a^8*r^6 + 3*(a^10 + 4*a^8*m^2)*r^4 - 4*(3*a^10*m + 2*a^8*m^3)*r^3 + 3*(a^12 + 4*a^10*m^2)*r^2)*y^8 + 4*(a^6*m - 2*a^4*m^3)*r^7 + 4*(a^12*m*r - 5*a^6*m*r^7 + a^6*r^8 + (3*a^8 + 8*a^6*m^2)*r^6 - (9*a^8*m + 4*a^6*m^3)*r^5 + (3*a^10 + 4*a^8*m^2)*r^4 - (3*a^10*m - 4*a^8*m^3)*r^3 + (a^12 - 4*a^10*m^2)*r^2)*y^6 + 2*(2*a^10*m^2*r^2 + 16*a^6*m^3*r^5 - 12*a^4*m*r^9 + 3*a^4*r^10 + (9*a^6 + 14*a^4*m^2)*r^8 - 2*(9*a^6*m + 2*a^4*m^3)*r^7 + 3*(3*a^8 - 2*a^6*m^2)*r^6 + 3*(a^10 - 6*a^8*m^2)*r^4 + 2*(3*a^10*m - 2*a^8*m^3)*r^3)*y^4 + 4*(2*a^8*m^2*r^4 - 3*a^4*m*r^9 - 3*a^2*m*r^11 + a^2*r^12 + (3*a^4 + 2*a^2*m^2)*r^10 + 3*(a^6 - 2*a^4*m^2)*r^8 + (3*a^6*m + 4*a^4*m^3)*r^7 + (a^8 - 6*a^6*m^2)*r^6 + (3*a^8*m - 4*a^6*m^3)*r^5)*y^2)

In [39]:
KK[1,2]

2*((a^8*m^2*r - a^6*m^2*r^3)*y^5 - (a^8*m^2*r + 3*a^4*m^2*r^5)*y^3 + (a^6*m^2*r^3 + 3*a^4*m^2*r^5)*y)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 + (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^8 + 4*(a^10*m*r - 2*a^8*m*r^3 - 3*a^6*m*r^5 + a^6*r^6 + 2*(a^8 + a^6*m^2)*r^4 + (a^10 - 2*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^4*m*r^7 + 3*a^4*r^8 + 2*(3*a^6 + a^4*m^2)*r^6 + (3*a^8 - 8*a^6*m^2)*r^4)*y^4 + 4*(2*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*a^4*m*r^7 + 2*a^4*r^8 - a^2*m*r^9 + a^2*r^10 + (a^6 - 2*a^4*m^2)*r^6)*y^2)

In [40]:
KK[1,3]

0

In [41]:
KK[2,2]

-4*((a^8*m^2*r^2 - 2*a^6*m^3*r^3 + a^6*m^2*r^4)*y^4 - (a^8*m^2*r^2 - 2*a^6*m^3*r^3 + a^6*m^2*r^4)*y^2)/(4*a^4*m^2*r^6 + 4*a^4*m*r^7 + a^4*r^8 + 4*a^2*m*r^9 + 2*a^2*r^10 + r^12 + (a^12 - 4*a^10*m*r - 4*a^8*m*r^3 + a^8*r^4 + 2*(a^10 + 2*a^8*m^2)*r^2)*y^8 + 4*(a^10*m*r - 2*a^8*m*r^3 - 3*a^6*m*r^5 + a^6*r^6 + 2*(a^8 + a^6*m^2)*r^4 + (a^10 - 2*a^8*m^2)*r^2)*y^6 + 2*(2*a^8*m^2*r^2 + 6*a^8*m*r^3 - 6*a^4*m*r^7 + 3*a^4*r^8 + 2*(3*a^6 + a^4*m^2)*r^6 + (3*a^8 - 8*a^6*m^2)*r^4)*y^4 + 4*(2*a^6*m^2*r^4 + 3*a^6*m*r^5 + 2*a^4*m*r^7 + 2*a^4*r^8 - a^2*m*r^9 + a^2*r^10 + (a^6 - 2*a^4*m^2)*r^6)*y^2)

In [42]:
KK[2,3]

0

In [43]:
KK[3,3]

(a^6*m^2*r^4 + 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8 + (a^10*m^2 - 6*a^8*m^2*r^2 + 8*a^6*m^3*r^3 - 3*a^6*m^2*r^4)*y^8 - 2*(a^10*m^2 - 7*a^8*m^2*r^2 + 12*a^6*m^3*r^3 - 3*a^6*m^2*r^4 - 3*a^4*m^2*r^6)*y^6 + (a^10*m^2 - 10*a^8*m^2*r^2 + 24*a^6*m^3*r^3 - 2*a^6*m^2*r^4 - 6*a^4*m^2*r^6 + 9*a^2*m^2*r^8)*y^4 + 2*(a^8*m^2*r^2 - 4*a^6*m^3*r^3 - a^6*m^2*r^4 - 3*a^4*m^2*r^6 - 9*a^2*m^2*r^8)*y^2)/(2*a^2*m*r^9 + a^2*r^10 + r^12 + (a^12 - 2*a^10*m*r + a^10*r^2)*y^10 + (2*a^10*m*r + 5*a^10*r^2 - 8*a^8*m*r^3 + 5*a^8*r^4)*y^8 + 2*(4*a^8*m*r^3 + 5*a^8*r^4 - 6*a^6*m*r^5 + 5*a^6*r^6)*y^6 + 2*(6*a^6*m*r^5 + 5*a^6*r^6 - 4*a^4*m*r^7 + 5*a^4*r^8)*y^4 + (8*a^4*m*r^7 + 5*a^4*r^8 - 2*a^2*m*r^9 + 5*a^2*r^10)*y^2)

<p>In vacuum and for stationary spacetimes, the dynamical Einstein equations are $$ \mathcal{L}_\beta K_{ij} - D_i D_j N + N \left( R_{ij} + K K_{ij} - 2 K_{ik} K^k_{\ \, j}\right) = 0 $$</p>

In [44]:
dyn = K.lie_der(b) - D(D(N)) + N*( Ric + trK*K - 2*KK )
print(dyn)
dyn.display()

Tensor field of type (0,2) on the 3-dimensional Riemannian manifold Sigma


0

<p>Hence, we have checked that all the vacuum 3+1 Einstein equations are fulfilled.</p>

<h2>Electric and magnetic parts of the Weyl tensor</h2>
<p>The electric part is the bilinear form $E$ given by 
$$E_{ij} = R_{ij} + K K_{ij} - K_{ik} K^k_{\ \, j} $$</p>

In [45]:
E = Ric + trK*K - KK
print(E)

Field of symmetric bilinear forms on the 3-dimensional Riemannian manifold Sigma


In [46]:
E[1,1]

-(3*a^4*m*r^3 - 2*a^2*m^2*r^4 + 5*a^2*m*r^5 + 2*m*r^7 + 3*(a^6*m*r - 2*a^4*m^2*r^2 + a^4*m*r^3)*y^4 - (9*a^6*m*r - 6*a^4*m^2*r^2 + 16*a^4*m*r^3 - 2*a^2*m^2*r^4 + 7*a^2*m*r^5)*y^2)/(2*a^4*m*r^5 + 2*a^2*r^8 - 2*m*r^9 + r^10 + (a^4 - 4*a^2*m^2)*r^6 + (a^10 - 4*a^8*m*r - 4*a^6*m*r^3 + a^6*r^4 + 2*(a^8 + 2*a^6*m^2)*r^2)*y^6 + (2*a^8*m*r - 8*a^6*m*r^3 - 10*a^4*m*r^5 + 3*a^4*r^6 + 2*(3*a^6 + 4*a^4*m^2)*r^4 + (3*a^8 - 4*a^6*m^2)*r^2)*y^4 + (4*a^6*m*r^3 - 4*a^4*m*r^5 - 8*a^2*m*r^7 + 3*a^2*r^8 + 2*(3*a^4 + 2*a^2*m^2)*r^6 + (3*a^6 - 8*a^4*m^2)*r^4)*y^2)

In [47]:
E[1,1].factor()

-(a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 - 3*a^4 + 2*a^2*m*r - 5*a^2*r^2 - 2*r^4)*(3*a^2*y^2 - r^2)*m*r/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2*(a^2 - 2*m*r + r^2))

In [48]:
E[1,2]

3*((a^6*m + a^4*m*r^2)*y^3 - 3*(a^4*m*r^2 + a^2*m*r^4)*y)/(2*a^2*m*r^5 + a^2*r^6 + r^8 + (a^8 - 2*a^6*m*r + a^6*r^2)*y^6 + (2*a^6*m*r + 3*a^6*r^2 - 4*a^4*m*r^3 + 3*a^4*r^4)*y^4 + (4*a^4*m*r^3 + 3*a^4*r^4 - 2*a^2*m*r^5 + 3*a^2*r^6)*y^2)

In [49]:
E[1,2].factor()

3*(a^2*y^2 - 3*r^2)*(a^2 + r^2)*a^2*m*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2)

In [50]:
E[1,3]

0

In [51]:
E[2,2]

-(3*a^4*m*r^3 - 4*a^2*m^2*r^4 + 4*a^2*m*r^5 + m*r^7 + 6*(a^6*m*r - 2*a^4*m^2*r^2 + a^4*m*r^3)*y^4 - (9*a^6*m*r - 12*a^4*m^2*r^2 + 14*a^4*m*r^3 - 4*a^2*m^2*r^4 + 5*a^2*m*r^5)*y^2)/((a^8 - 2*a^6*m*r + a^6*r^2)*y^8 - 2*a^2*m*r^5 - a^2*r^6 - r^8 - (a^8 - 4*a^6*m*r - 2*a^6*r^2 + 4*a^4*m*r^3 - 3*a^4*r^4)*y^6 - (2*a^6*m*r + 3*a^6*r^2 - 8*a^4*m*r^3 + 2*a^2*m*r^5 - 3*a^2*r^6)*y^4 - (4*a^4*m*r^3 + 3*a^4*r^4 - 4*a^2*m*r^5 + 2*a^2*r^6 - r^8)*y^2)

In [52]:
E[2,2].factor()

-(2*a^4*y^2 - 4*a^2*m*r*y^2 + 2*a^2*r^2*y^2 - 3*a^4 + 4*a^2*m*r - 4*a^2*r^2 - r^4)*(3*a^2*y^2 - r^2)*m*r/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2*(y + 1)*(y - 1))

In [53]:
E[2,3]

0

In [54]:
E[3,3]

(2*a^2*m^2*r^4 + a^2*m*r^5 + m*r^7 + 3*(a^6*m*r - 2*a^4*m^2*r^2 + a^4*m*r^3)*y^6 - (3*a^6*m*r - 12*a^4*m^2*r^2 + a^4*m*r^3 - 2*a^2*m^2*r^4 - 2*a^2*m*r^5)*y^4 - (6*a^4*m^2*r^2 + 2*a^4*m*r^3 + 4*a^2*m^2*r^4 + 3*a^2*m*r^5 + m*r^7)*y^2)/(a^8*y^8 + 4*a^6*r^2*y^6 + 6*a^4*r^4*y^4 + 4*a^2*r^6*y^2 + r^8)

In [55]:
E[3,3].factor()

(a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(3*a^2*y^2 - r^2)*m*r*(y + 1)*(y - 1)/(a^2*y^2 + r^2)^4

<p>The magnetic part is the bilinear form $B$ defined by $$ B_{ij} = \epsilon^k_{\ \, l i} D_k K^l_{\ \, j}, $$</p>
<p>where $\epsilon^k_{\ \, l i}$ are the components of the type-(1,2) tensor $\epsilon^\sharp$, related to the Levi-Civita alternating tensor $\epsilon$ associated with $\gamma$ by $\epsilon^k_{\ \, l i} = \gamma^{km} \epsilon_{m l i}$. In SageManifolds, $\epsilon$ is obtained by the command <span style="font-family: courier new,courier;">volume_form()</span> and $\epsilon^\sharp$ by the command <span style="font-family: courier new,courier;">volume_form(1)</span> (1 = 1 index raised):</p>

In [56]:
eps = gam.volume_form() 
print(eps) ; eps.display()

3-form eps_gam on the 3-dimensional Riemannian manifold Sigma


eps_gam = sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2*y^2 + r^2)/sqrt(a^2 - 2*m*r + r^2) dr/\dy/\dph

In [57]:
epsu = gam.volume_form(1)
print(epsu) ; epsu.display()

Tensor field of type (1,2) on the 3-dimensional Riemannian manifold Sigma


sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)/sqrt(a^2*y^2 + r^2) d/dr*dy*dph - sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)/sqrt(a^2*y^2 + r^2) d/dr*dph*dy + sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(y^2 - 1)/(sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) d/dy*dr*dph - sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(y^2 - 1)/(sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)) d/dy*dph*dr - sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(a^2*y^2 + r^2)^(3/2)/(((a^4 - 2*a^2*m*r + a^2*r^2)*y^4 - 2*a^2*m*r - a^2*r^2 - r^4 - (a^4 - 4*a^2*m*r - r^4)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dph*dr*dy + sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(a^2*y^2 + r^2)^(3/2)/(((a^4 - 2*a^2*m*r + a^2*r^2)*y^4 - 2*a^2*m*r - a^2*r^2 - r^4 - (a^4 - 4*a^2*m*r - r^4)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dph*dy*dr

In [58]:
DKu = D(Ku)
B = epsu['^k_li']*DKu['^l_jk'] 
print(B)

Tensor field of type (0,2) on the 3-dimensional Riemannian manifold Sigma


<p>Let us check that $B$ is symmetric:</p>

In [59]:
B1 = B.symmetrize()
B == B1

True

<p>Accordingly, we set</p>

In [60]:
B = B1
B.set_name('B')
print(B)

Field of symmetric bilinear forms B on the 3-dimensional Riemannian manifold Sigma


In [61]:
B[1,1]

-((a^7*m - 2*a^5*m^2*r + a^5*m*r^2)*y^5 - (3*a^7*m - 2*a^5*m^2*r + 8*a^5*m*r^2 - 6*a^3*m^2*r^3 + 5*a^3*m*r^4)*y^3 + 3*(3*a^5*m*r^2 - 2*a^3*m^2*r^3 + 5*a^3*m*r^4 + 2*a*m*r^6)*y)/(2*a^4*m*r^5 + 2*a^2*r^8 - 2*m*r^9 + r^10 + (a^4 - 4*a^2*m^2)*r^6 + (a^10 - 4*a^8*m*r - 4*a^6*m*r^3 + a^6*r^4 + 2*(a^8 + 2*a^6*m^2)*r^2)*y^6 + (2*a^8*m*r - 8*a^6*m*r^3 - 10*a^4*m*r^5 + 3*a^4*r^6 + 2*(3*a^6 + 4*a^4*m^2)*r^4 + (3*a^8 - 4*a^6*m^2)*r^2)*y^4 + (4*a^6*m*r^3 - 4*a^4*m*r^5 - 8*a^2*m*r^7 + 3*a^2*r^8 + 2*(3*a^4 + 2*a^2*m^2)*r^6 + (3*a^6 - 8*a^4*m^2)*r^4)*y^2)

In [62]:
B[1,1].factor()

-(a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 - 3*a^4 + 2*a^2*m*r - 5*a^2*r^2 - 2*r^4)*(a^2*y^2 - 3*r^2)*a*m*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2*(a^2 - 2*m*r + r^2))

In [63]:
B[1,2]

3*(a^3*m*r^3 + a*m*r^5 - 3*(a^5*m*r + a^3*m*r^3)*y^2)/(2*a^2*m*r^5 + a^2*r^6 + r^8 + (a^8 - 2*a^6*m*r + a^6*r^2)*y^6 + (2*a^6*m*r + 3*a^6*r^2 - 4*a^4*m*r^3 + 3*a^4*r^4)*y^4 + (4*a^4*m*r^3 + 3*a^4*r^4 - 2*a^2*m*r^5 + 3*a^2*r^6)*y^2)

In [64]:
B[1,2].factor()

-3*(3*a^2*y^2 - r^2)*(a^2 + r^2)*a*m*r/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2)

In [65]:
B[1,3]

0

In [66]:
B[2,2]

-(2*(a^7*m - 2*a^5*m^2*r + a^5*m*r^2)*y^5 - (3*a^7*m - 4*a^5*m^2*r + 10*a^5*m*r^2 - 12*a^3*m^2*r^3 + 7*a^3*m*r^4)*y^3 + 3*(3*a^5*m*r^2 - 4*a^3*m^2*r^3 + 4*a^3*m*r^4 + a*m*r^6)*y)/((a^8 - 2*a^6*m*r + a^6*r^2)*y^8 - 2*a^2*m*r^5 - a^2*r^6 - r^8 - (a^8 - 4*a^6*m*r - 2*a^6*r^2 + 4*a^4*m*r^3 - 3*a^4*r^4)*y^6 - (2*a^6*m*r + 3*a^6*r^2 - 8*a^4*m*r^3 + 2*a^2*m*r^5 - 3*a^2*r^6)*y^4 - (4*a^4*m*r^3 + 3*a^4*r^4 - 4*a^2*m*r^5 + 2*a^2*r^6 - r^8)*y^2)

In [67]:
B[2,2].factor()

-(2*a^4*y^2 - 4*a^2*m*r*y^2 + 2*a^2*r^2*y^2 - 3*a^4 + 4*a^2*m*r - 4*a^2*r^2 - r^4)*(a^2*y^2 - 3*r^2)*a*m*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^2*(y + 1)*(y - 1))

In [68]:
B[2,3]

0

In [69]:
B[3,3]

((a^7*m - 2*a^5*m^2*r + a^5*m*r^2)*y^7 - (a^7*m - 4*a^5*m^2*r + 3*a^5*m*r^2 - 6*a^3*m^2*r^3 + 2*a^3*m*r^4)*y^5 - (2*a^5*m^2*r - 2*a^5*m*r^2 + 12*a^3*m^2*r^3 + a^3*m*r^4 + 3*a*m*r^6)*y^3 + 3*(2*a^3*m^2*r^3 + a^3*m*r^4 + a*m*r^6)*y)/(a^8*y^8 + 4*a^6*r^2*y^6 + 6*a^4*r^4*y^4 + 4*a^2*r^6*y^2 + r^8)

In [70]:
B[3,3].factor()

(a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 - 3*r^2)*a*m*(y + 1)*(y - 1)*y/(a^2*y^2 + r^2)^4

<h2>3+1 decomposition of the Simon-Mars tensor</h2>
<p>We follow the computation presented in <a href="http://arxiv.org/abs/1412.6542">arXiv:1412.6542</a>. We start by the tensor $E^\sharp$ of components $E^i_ {\ \, j}$:</p>

In [71]:
Eu = E.up(gam, 0) 
print(Eu)

Tensor field of type (1,1) on the 3-dimensional Riemannian manifold Sigma


<p>Tensor $B^\sharp$ of components $B^i_{\ \, j}$:</p>

In [72]:
Bu = B.up(gam, 0)
print(Bu)

Tensor field of type (1,1) on the 3-dimensional Riemannian manifold Sigma


<p>1-form $\beta^\flat$ of components $\beta_i$ and its exterior derivative:</p>

In [73]:
bd = b.down(gam)
xdb = bd.exterior_derivative()
print(xdb) ; xdb.display()

2-form on the 3-dimensional Riemannian manifold Sigma


2*(a^3*m*y^4 + a*m*r^2 - (a^3*m + a*m*r^2)*y^2)/(a^4*y^4 + 2*a^2*r^2*y^2 + r^4) dr/\dph + 4*(a^3*m*r + a*m*r^3)*y/(a^4*y^4 + 2*a^2*r^2*y^2 + r^4) dy/\dph

<p>Scalar square of shift $\beta_i \beta^i$:</p>

In [74]:
b2 = bd(b)
print(b2) ; b2.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> -4*(a^2*m^2*r^2*y^2 - a^2*m^2*r^2)/(2*a^2*m*r^3 + a^2*r^4 + r^6 + (a^6 - 2*a^4*m*r + a^4*r^2)*y^4 + 2*(a^4*m*r + a^4*r^2 - a^2*m*r^3 + a^2*r^4)*y^2)

<p>Scalar $Y = E(\beta,\beta) = E_{ij} \beta^i \beta^j$:</p>

In [75]:
Ebb = E(b,b)
Y = Ebb
print(Y) ; Y.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> 4*(3*a^4*m^3*r^3*y^4 + a^2*m^3*r^5 - (3*a^4*m^3*r^3 + a^2*m^3*r^5)*y^2)/(2*a^2*m*r^9 + a^2*r^10 + r^12 + (a^12 - 2*a^10*m*r + a^10*r^2)*y^10 + (2*a^10*m*r + 5*a^10*r^2 - 8*a^8*m*r^3 + 5*a^8*r^4)*y^8 + 2*(4*a^8*m*r^3 + 5*a^8*r^4 - 6*a^6*m*r^5 + 5*a^6*r^6)*y^6 + 2*(6*a^6*m*r^5 + 5*a^6*r^6 - 4*a^4*m*r^7 + 5*a^4*r^8)*y^4 + (8*a^4*m*r^7 + 5*a^4*r^8 - 2*a^2*m*r^9 + 5*a^2*r^10)*y^2)

In [76]:
Ebb.coord_function().factor()

4*(3*a^2*y^2 - r^2)*a^2*m^3*r^3*(y + 1)*(y - 1)/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^4)

In [77]:
Ebb.display()

Sigma --> R
(r, y, ph) |--> 4*(3*a^2*y^2 - r^2)*a^2*m^3*r^3*(y + 1)*(y - 1)/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^4)

<p>Scalar $\bar Y = B(\beta,\beta) = B_{ij}\beta^i \beta^j$:</p>

In [78]:
Bbb = B(b,b)
Y_bar = Bbb
print(Y_bar) ; Y_bar.display()

Scalar field B(beta,beta) on the 3-dimensional Riemannian manifold Sigma


B(beta,beta): Sigma --> R
   (r, y, ph) |--> 4*(a^5*m^3*r^2*y^5 + 3*a^3*m^3*r^4*y - (a^5*m^3*r^2 + 3*a^3*m^3*r^4)*y^3)/(2*a^2*m*r^9 + a^2*r^10 + r^12 + (a^12 - 2*a^10*m*r + a^10*r^2)*y^10 + (2*a^10*m*r + 5*a^10*r^2 - 8*a^8*m*r^3 + 5*a^8*r^4)*y^8 + 2*(4*a^8*m*r^3 + 5*a^8*r^4 - 6*a^6*m*r^5 + 5*a^6*r^6)*y^6 + 2*(6*a^6*m*r^5 + 5*a^6*r^6 - 4*a^4*m*r^7 + 5*a^4*r^8)*y^4 + (8*a^4*m*r^7 + 5*a^4*r^8 - 2*a^2*m*r^9 + 5*a^2*r^10)*y^2)

In [79]:
Bbb.coord_function().factor()

4*(a^2*y^2 - 3*r^2)*a^3*m^3*r^2*(y + 1)*(y - 1)*y/((a^4*y^2 - 2*a^2*m*r*y^2 + a^2*r^2*y^2 + 2*a^2*m*r + a^2*r^2 + r^4)*(a^2*y^2 + r^2)^4)

<p>1-form of components $Eb_i = E_{ij} \beta^j$:</p>

In [80]:
Eb = E.contract(b)
print(Eb) ; Eb.display()

1-form on the 3-dimensional Riemannian manifold Sigma


-2*(3*a^3*m^2*r^2*y^4 + a*m^2*r^4 - (3*a^3*m^2*r^2 + a*m^2*r^4)*y^2)/(a^8*y^8 + 4*a^6*r^2*y^6 + 6*a^4*r^4*y^4 + 4*a^2*r^6*y^2 + r^8) dph

<p>Vector field of components $Eub^i = E^i_{\ \, j} \beta^j$:</p>

In [81]:
Eub = Eu.contract(b)
print(Eub) ; Eub.display()

Vector field on the 3-dimensional Riemannian manifold Sigma


2*(3*a^3*m^2*r^2*y^2 - a*m^2*r^4)/(2*a^2*m*r^7 + a^2*r^8 + r^10 + (a^10 - 2*a^8*m*r + a^8*r^2)*y^8 + 2*(a^8*m*r + 2*a^8*r^2 - 3*a^6*m*r^3 + 2*a^6*r^4)*y^6 + 6*(a^6*m*r^3 + a^6*r^4 - a^4*m*r^5 + a^4*r^6)*y^4 + 2*(3*a^4*m*r^5 + 2*a^4*r^6 - a^2*m*r^7 + 2*a^2*r^8)*y^2) d/dph

<p>1-form of components $Bb_i = B_{ij} \beta^j$:</p>

In [82]:
Bb = B.contract(b)
print(Bb) ; Bb.display()

1-form on the 3-dimensional Riemannian manifold Sigma


-2*(a^4*m^2*r*y^5 + 3*a^2*m^2*r^3*y - (a^4*m^2*r + 3*a^2*m^2*r^3)*y^3)/(a^8*y^8 + 4*a^6*r^2*y^6 + 6*a^4*r^4*y^4 + 4*a^2*r^6*y^2 + r^8) dph

<p>Vector field of components $Bub^i = B^i_{\ \, j} \beta^j$:</p>

In [83]:
Bub = Bu.contract(b)
print(Bub) ; Bub.display()

Vector field on the 3-dimensional Riemannian manifold Sigma


2*(a^4*m^2*r*y^3 - 3*a^2*m^2*r^3*y)/(2*a^2*m*r^7 + a^2*r^8 + r^10 + (a^10 - 2*a^8*m*r + a^8*r^2)*y^8 + 2*(a^8*m*r + 2*a^8*r^2 - 3*a^6*m*r^3 + 2*a^6*r^4)*y^6 + 6*(a^6*m*r^3 + a^6*r^4 - a^4*m*r^5 + a^4*r^6)*y^4 + 2*(3*a^4*m*r^5 + 2*a^4*r^6 - a^2*m*r^7 + 2*a^2*r^8)*y^2) d/dph

<p>Vector field of components $Kub^i = K^i_{\ \, j} \beta^j$:</p>

In [84]:
Kub = Ku.contract(b)
print(Kub) ; Kub.display()

Vector field on the 3-dimensional Riemannian manifold Sigma


-2*(a^6*m^2*r^3 - 2*a^4*m^3*r^4 + 4*a^4*m^2*r^5 - 6*a^2*m^3*r^6 + 3*a^2*m^2*r^7 + (a^8*m^2*r - 2*a^6*m^3*r^2 + 2*a^4*m^3*r^4 - a^4*m^2*r^5)*y^4 - (a^8*m^2*r - 2*a^6*m^3*r^2 + a^6*m^2*r^3 + 3*a^4*m^2*r^5 - 6*a^2*m^3*r^6 + 3*a^2*m^2*r^7)*y^2)*sqrt(a^2*y^2 + r^2)/((2*a^2*m*r^7 + a^2*r^8 + r^10 + (a^10 - 2*a^8*m*r + a^8*r^2)*y^8 + 2*(a^8*m*r + 2*a^8*r^2 - 3*a^6*m*r^3 + 2*a^6*r^4)*y^6 + 6*(a^6*m*r^3 + a^6*r^4 - a^4*m*r^5 + a^4*r^6)*y^4 + 2*(3*a^4*m*r^5 + 2*a^4*r^6 - a^2*m*r^7 + 2*a^2*r^8)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)) d/dr - 4*(a^4*m^2*r^2*y^5 - 2*a^4*m^2*r^2*y^3 + a^4*m^2*r^2*y)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)/((2*a^2*m*r^7 + a^2*r^8 + r^10 + (a^10 - 2*a^8*m*r + a^8*r^2)*y^8 + 2*(a^8*m*r + 2*a^8*r^2 - 3*a^6*m*r^3 + 2*a^6*r^4)*y^6 + 6*(a^6*m*r^3 + a^6*r^4 - a^4*m*r^5 + a^4*r^6)*y^4 + 2*(3*a^4*m*r^5 + 2*a^4*r^6 - a^2*m*r^7 + 2*a^2*r^8)*y^2)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)) d/dy

In [85]:
T = 2*b(N) - 2*K(b,b)
print(T) ; T.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> 0

In [86]:
Db = D(b)  #  Db^i_j = D_j b^i
Dbu = Db.up(gam, 1)  # Dbu^{ij} = D^j b^i
bDb = b*Dbu  # bDb^{ijk} = b^i D^k b^j
T_bar = eps['_ijk']*bDb['^ikj']
print(T_bar) ; T_bar.display()

Scalar field zero on the 3-dimensional Riemannian manifold Sigma


zero: Sigma --> R
   (r, y, ph) |--> 0

In [87]:
epsb = eps.contract(b) 
print(epsb)
epsb.display()

2-form on the 3-dimensional Riemannian manifold Sigma


-2*sqrt(a^2*y^2 + r^2)*a*m*r/(sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2 - 2*m*r + r^2)) dr/\dy

In [88]:
epsB = eps['_ijl']*Bu['^l_k']
print(epsB)

Tensor field of type (0,3) on the 3-dimensional Riemannian manifold Sigma


In [89]:
epsB.symmetries()

no symmetry; antisymmetry: (0, 1)


In [90]:
epsB[1,2,3]

-(a^3*m*y^3 - 3*a*m*r^2*y)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*sqrt(a^2*y^2 + r^2)/((a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)*sqrt(a^2 - 2*m*r + r^2))

In [91]:
Z = 2*N*( D(N)  -K.contract(b)) + b.contract(xdb)
print(Z) ; Z.display()

1-form on the 3-dimensional Riemannian manifold Sigma


-2*(a^2*m*y^2 - m*r^2)/(a^4*y^4 + 2*a^2*r^2*y^2 + r^4) dr + 4*a^2*m*r*y/(a^4*y^4 + 2*a^2*r^2*y^2 + r^4) dy

In [92]:
DNu = D(N).up(gam)
A = 2*(DNu - Ku.contract(b))*b + N*Dbu
Z_bar = eps['_ijk']*A['^kj']
print(Z_bar) ; Z_bar.display()

1-form on the 3-dimensional Riemannian manifold Sigma


4*a*m*r*y/(a^4*y^4 + 2*a^2*r^2*y^2 + r^4) dr + 2*(a^3*m*y^2 - a*m*r^2)/(a^4*y^4 + 2*a^2*r^2*y^2 + r^4) dy

In [93]:
# Test:
Dbdu = D(bd).up(gam,1).up(gam,1)  # (Db)^{ij} = D^i b^j
A = 2*b*(DNu - Ku.contract(b)) + N*Dbdu
Z_bar0 = eps['_ijk']*A['^jk']  # NB: '^jk' and not 'kj'
Z_bar0 == Z_bar

True

In [94]:
W = N*Eb + epsb.contract(Bub)
print(W) ; W.display()

1-form on the 3-dimensional Riemannian manifold Sigma


-2*(3*a^3*m^2*r^2*y^4 + a*m^2*r^4 - (3*a^3*m^2*r^2 + a*m^2*r^4)*y^2)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)/((a^8*y^8 + 4*a^6*r^2*y^6 + 6*a^4*r^4*y^4 + 4*a^2*r^6*y^2 + r^8)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)) dph

In [95]:
W_bar = N*Bb - epsb.contract(Eub)
print(W_bar) ; W_bar.display()

1-form on the 3-dimensional Riemannian manifold Sigma


-2*(a^4*m^2*r*y^5 + 3*a^2*m^2*r^3*y - (a^4*m^2*r + 3*a^2*m^2*r^3)*y^3)*sqrt(a^2*y^2 + r^2)*sqrt(a^2 - 2*m*r + r^2)/((a^8*y^8 + 4*a^6*r^2*y^6 + 6*a^4*r^4*y^4 + 4*a^2*r^6*y^2 + r^8)*sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)) dph

In [96]:
W[3].factor()

-2*(3*a^2*y^2 - r^2)*sqrt(a^2 - 2*m*r + r^2)*a*m^2*r^2*(y + 1)*(y - 1)/(sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(a^2*y^2 + r^2)^(7/2))

In [97]:
W_bar[3].factor()

-2*(a^2*y^2 - 3*r^2)*sqrt(a^2 - 2*m*r + r^2)*a^2*m^2*r*(y + 1)*(y - 1)*y/(sqrt(2*a^2*m*r + a^2*r^2 + r^4 + (a^4 - 2*a^2*m*r + a^2*r^2)*y^2)*(a^2*y^2 + r^2)^(7/2))

In [98]:
M = - 4*Eb(Kub - DNu) - 2*(epsB['_ij.']*Dbu['^ji'])(b)
print(M) ; M.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> 0

In [99]:
M_bar = 2*(eps.contract(Eub))['_ij']*Dbu['^ji'] - 4*Bb(Kub - DNu)
print(M_bar) ; M_bar.display()

Scalar field on the 3-dimensional Riemannian manifold Sigma


Sigma --> R
(r, y, ph) |--> 0

In [100]:
A = epsB['_ilk']*b['^l'] + epsB['_ikl']*b['^l'] \
    + Bu['^m_i']*epsb['_mk'] - 2*N*E
xdbE = xdb['_kl']*Eu['^k_i']
L = 2*N*epsB['_kli']*Dbu['^kl'] + 2*xdb['_ij']*Eub['^j'] \
    + 2*xdbE['_li']*b['^l'] + 2*A['_ik']*(Kub - DNu)['^k']
print(L)

1-form on the 3-dimensional Riemannian manifold Sigma


In [101]:
L[1]

-8*(5*a^4*m^2*r*y^4 - 10*a^2*m^2*r^3*y^2 + m^2*r^5)/(a^10*y^10 + 5*a^8*r^2*y^8 + 10*a^6*r^4*y^6 + 10*a^4*r^6*y^4 + 5*a^2*r^8*y^2 + r^10)

In [102]:
L[1].factor()

-8*(5*a^4*y^4 - 10*a^2*r^2*y^2 + r^4)*m^2*r/(a^2*y^2 + r^2)^5

In [103]:
L[2]

-8*(a^6*m^2*y^5 - 10*a^4*m^2*r^2*y^3 + 5*a^2*m^2*r^4*y)/(a^10*y^10 + 5*a^8*r^2*y^8 + 10*a^6*r^4*y^6 + 10*a^4*r^6*y^4 + 5*a^2*r^8*y^2 + r^10)

In [104]:
L[2].factor()

-8*(a^4*y^4 - 10*a^2*r^2*y^2 + 5*r^4)*a^2*m^2*y/(a^2*y^2 + r^2)^5

In [105]:
L[3]

0

In [106]:
N2pbb = N^2 + b2
V = N2pbb*E - 2*(b.contract(E)*bd).symmetrize() + Ebb*gam \
    + 2*N*(b.contract(epsB).symmetrize())
print(V)

Field of symmetric bilinear forms on the 3-dimensional Riemannian manifold Sigma


In [107]:
V[1,1]

-(3*a^4*m*r*y^4 + 3*a^2*m*r^3 - 4*m^2*r^4 + 2*m*r^5 - (9*a^4*m*r - 12*a^2*m^2*r^2 + 7*a^2*m*r^3)*y^2)/(a^2*r^6 - 2*m*r^7 + r^8 + (a^8 - 2*a^6*m*r + a^6*r^2)*y^6 + 3*(a^6*r^2 - 2*a^4*m*r^3 + a^4*r^4)*y^4 + 3*(a^4*r^4 - 2*a^2*m*r^5 + a^2*r^6)*y^2)

In [108]:
V[1,1].factor()

-(3*a^2*y^2 - r^2)*(a^2*y^2 - 3*a^2 + 4*m*r - 2*r^2)*m*r/((a^2*y^2 + r^2)^3*(a^2 - 2*m*r + r^2))

In [109]:
V[1,2]

3*(a^4*m*y^3 - 3*a^2*m*r^2*y)/(a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)

In [110]:
V[1,2].factor()

3*(a^2*y^2 - 3*r^2)*a^2*m*y/(a^2*y^2 + r^2)^3

In [111]:
V[1,3]

0

In [112]:
V[2,2]

-(6*a^4*m*r*y^4 + 3*a^2*m*r^3 - 2*m^2*r^4 + m*r^5 - (9*a^4*m*r - 6*a^2*m^2*r^2 + 5*a^2*m*r^3)*y^2)/(a^6*y^8 - (a^6 - 3*a^4*r^2)*y^6 - r^6 - 3*(a^4*r^2 - a^2*r^4)*y^4 - (3*a^2*r^4 - r^6)*y^2)

In [113]:
V[2,2].factor()

-(3*a^2*y^2 - r^2)*(2*a^2*y^2 - 3*a^2 + 2*m*r - r^2)*m*r/((a^2*y^2 + r^2)^3*(y + 1)*(y - 1))

In [114]:
V[2,3]

0

In [115]:
V[3,3]

(a^2*m*r^3 - 2*m^2*r^4 + m*r^5 + 3*(a^4*m*r - 2*a^2*m^2*r^2 + a^2*m*r^3)*y^4 - (3*a^4*m*r - 6*a^2*m^2*r^2 + 4*a^2*m*r^3 - 2*m^2*r^4 + m*r^5)*y^2)/(a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)

In [116]:
V[3,3].factor()

(3*a^2*y^2 - r^2)*(a^2 - 2*m*r + r^2)*m*r*(y + 1)*(y - 1)/(a^2*y^2 + r^2)^3

In [117]:
beps = b.contract(eps)
V_bar = N2pbb*B - 2*(b.contract(B)*bd).symmetrize() + Bbb*gam \
        - 2*N*(beps['_il']*Eu['^l_j']).symmetrize()
print(V_bar)

Field of symmetric bilinear forms on the 3-dimensional Riemannian manifold Sigma


In [118]:
V_bar[1,1]

-(a^5*m*y^5 - (3*a^5*m - 4*a^3*m^2*r + 5*a^3*m*r^2)*y^3 + 3*(3*a^3*m*r^2 - 4*a*m^2*r^3 + 2*a*m*r^4)*y)/(a^2*r^6 - 2*m*r^7 + r^8 + (a^8 - 2*a^6*m*r + a^6*r^2)*y^6 + 3*(a^6*r^2 - 2*a^4*m*r^3 + a^4*r^4)*y^4 + 3*(a^4*r^4 - 2*a^2*m*r^5 + a^2*r^6)*y^2)

In [119]:
V_bar[1,1].factor()

-(a^2*y^2 - 3*a^2 + 4*m*r - 2*r^2)*(a^2*y^2 - 3*r^2)*a*m*y/((a^2*y^2 + r^2)^3*(a^2 - 2*m*r + r^2))

In [120]:
V_bar[1,2]

-3*(3*a^3*m*r*y^2 - a*m*r^3)/(a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)

In [121]:
V_bar[1,2].factor()

-3*(3*a^2*y^2 - r^2)*a*m*r/(a^2*y^2 + r^2)^3

In [122]:
V_bar[1,3]

0

In [123]:
V_bar[2,2]

-(2*a^5*m*y^5 - (3*a^5*m - 2*a^3*m^2*r + 7*a^3*m*r^2)*y^3 + 3*(3*a^3*m*r^2 - 2*a*m^2*r^3 + a*m*r^4)*y)/(a^6*y^8 - (a^6 - 3*a^4*r^2)*y^6 - r^6 - 3*(a^4*r^2 - a^2*r^4)*y^4 - (3*a^2*r^4 - r^6)*y^2)

In [124]:
V_bar[2,2].factor()

-(2*a^2*y^2 - 3*a^2 + 2*m*r - r^2)*(a^2*y^2 - 3*r^2)*a*m*y/((a^2*y^2 + r^2)^3*(y + 1)*(y - 1))

In [125]:
V_bar[2,3]

0

In [126]:
V_bar[3,3]

((a^5*m - 2*a^3*m^2*r + a^3*m*r^2)*y^5 - (a^5*m - 2*a^3*m^2*r + 4*a^3*m*r^2 - 6*a*m^2*r^3 + 3*a*m*r^4)*y^3 + 3*(a^3*m*r^2 - 2*a*m^2*r^3 + a*m*r^4)*y)/(a^6*y^6 + 3*a^4*r^2*y^4 + 3*a^2*r^4*y^2 + r^6)

In [127]:
V_bar[3,3].factor()

(a^2*y^2 - 3*r^2)*(a^2 - 2*m*r + r^2)*a*m*(y + 1)*(y - 1)*y/(a^2*y^2 + r^2)^3

In [128]:
G = (N^2 - b2)*gam + bd*bd
print(G)

Field of symmetric bilinear forms on the 3-dimensional Riemannian manifold Sigma


In [129]:
G.display()

(a^2*y^2 - 2*m*r + r^2)/(a^2 - 2*m*r + r^2) dr*dr - (a^2*y^2 - 2*m*r + r^2)/(y^2 - 1) dy*dy + (-(a^2 - 2*m*r + r^2)*y^2 + a^2 - 2*m*r + r^2) dph*dph

<h3>3+1 decomposition of the real part of the Simon-Mars tensor</h3>
<p>We follow Eqs. (77)-(80) of <a href="http://arxiv.org/abs/1412.6542">arXiv:1412.6542</a>:</p>

In [130]:
S1 = (4*(V*Z - V_bar*Z_bar) + G*L).antisymmetrize(1,2)
print(S1)

Tensor field of type (0,3) on the 3-dimensional Riemannian manifold Sigma


In [131]:
S1.display()

0

In [132]:
S2 = 4*(T*V - T_bar*V_bar - W*Z + W_bar*Z_bar) + M*G \
     - N*bd*L
print(S2)

Tensor field of type (0,2) on the 3-dimensional Riemannian manifold Sigma


In [133]:
S2.display()

0

In [134]:
S3 = (4*(W*Z - W_bar*Z_bar) + N*bd*L).antisymmetrize()
print(S3)

2-form on the 3-dimensional Riemannian manifold Sigma


In [135]:
S3.display()

0

In [136]:
S2[3,1] == -2*S3[3,1]

True

In [137]:
S2[3,2] == -2*S3[3,2]

True

In [138]:
S4 = 4*(T*W - T_bar*W_bar) -4*(Y*Z - Y_bar*Z_bar) + N*M*bd \
     - b2*L
print(S4)

1-form on the 3-dimensional Riemannian manifold Sigma


In [139]:
S4.display()

0

<p>Hence all the tensors $S^1$, $S^2$, $S^3$ and $S^4$ involved in the 3+1 decomposition of the real part of the Simon-Mars are zero, as they should since the Simon-Mars tensor vanishes identically for the Kerr spacetime.</p>

<h3>3+1 decomposition of the imaginary part of the Simon-Mars tensor</h3>

<p>We follow Eqs. (82)-(85) of <a href="http://arxiv.org/abs/1412.6542">arXiv:1412.6542</a>.</p>

In [140]:
epsE = eps['_ijl']*Eu['^l_k']
print(epsE)

Tensor field of type (0,3) on the 3-dimensional Riemannian manifold Sigma


In [141]:
A = - epsE['_ilk']*b['^l'] - epsE['_ikl']*b['^l'] \
     - Eu['^m_i']*epsb['_mk'] - 2*N*B
xdbB = xdb['_kl']*Bu['^k_i']
L_bar = - 2*N*epsE['_kli']*Dbu['^kl'] \
        + 2*xdb['_ij']*Bub['^j'] + 2*xdbB['_li']*b['^l'] \
        + 2*A['_ik']*(Kub - DNu)['^k']
print(L_bar)

1-form on the 3-dimensional Riemannian manifold Sigma


In [142]:
L_bar.display()

-8*(a^5*m^2*y^5 - 10*a^3*m^2*r^2*y^3 + 5*a*m^2*r^4*y)/(a^10*y^10 + 5*a^8*r^2*y^8 + 10*a^6*r^4*y^6 + 10*a^4*r^6*y^4 + 5*a^2*r^8*y^2 + r^10) dr + 8*(5*a^5*m^2*r*y^4 - 10*a^3*m^2*r^3*y^2 + a*m^2*r^5)/(a^10*y^10 + 5*a^8*r^2*y^8 + 10*a^6*r^4*y^6 + 10*a^4*r^6*y^4 + 5*a^2*r^8*y^2 + r^10) dy

In [143]:
S1_bar = (4*(V*Z_bar + V_bar*Z) + G*L_bar).antisymmetrize(1,2)
print(S1_bar)

Tensor field of type (0,3) on the 3-dimensional Riemannian manifold Sigma


In [144]:
S1_bar.display()

0

In [145]:
S2_bar = 4*(T_bar*V + T*V_bar) - 4*(W*Z_bar + W_bar*Z) \
         + M_bar*G - N*bd*L_bar
print(S2_bar)

Tensor field of type (0,2) on the 3-dimensional Riemannian manifold Sigma


In [146]:
S2_bar.display()

0

In [147]:
S3_bar = (4*(W*Z_bar + W_bar*Z) + N*bd*L_bar).antisymmetrize()
print(S3_bar)

2-form on the 3-dimensional Riemannian manifold Sigma


In [148]:
S3_bar.display()

0

In [149]:
S4_bar = 4*(T_bar*W + T*W_bar - Y*Z_bar - Y_bar*Z) \
         + M_bar*N*bd - b2*L_bar
print(S4_bar)

1-form on the 3-dimensional Riemannian manifold Sigma


In [150]:
S4_bar.display()

0

<p>Hence all the tensors ${\bar S}^1$, ${\bar S}^2$, ${\bar S}^3$ and ${\bar S}^4$ involved in the 3+1 decomposition of the imaginary part of the Simon-Mars are zero, as they should since the Simon-Mars tensor vanishes identically for the Kerr spacetime.</p>